<a href="https://colab.research.google.com/github/DeepakSaiPaty/Deepaksai_INFO5731_Spring2020/blob/master/Copy_of_INFO5731_Assignment_Three.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# **INFO5731 Assignment Three**

In this assignment, you are required to conduct information extraction, semantic analysis based on **the dataset you collected from assignment two**. You may use scipy and numpy package in this assignment.

# **Question 1: Understand N-gram**

(45 points). Write a python program to conduct N-gram analysis based on the dataset in your assignment two:

(1) Count the frequency of all the N-grams (N=3).

(2) Calculate the probabilities for all the bigrams in the dataset by using the fomular count(w2 w1) / count(w2). For example, count(really like) / count(really) = 1 / 3 = 0.33.

(3) Extract all the **noun phrases** and calculate the relative probabilities of each review in terms of other reviews (abstracts, or tweets) by using the fomular frequency (noun phrase) / max frequency (noun phrase) on the whole dataset. Print out the result in a table with column name the all the noun phrases and row name as all the 100 reviews (abstracts, or tweets). 


In [0]:
# Write your code here
    !apt-get update
    !apt install chromium-chromedriver
    !cp /usr/lib/chromium-browser/chromedriver /usr/bin
    !pip install selenium

Get:1 https://cloud.r-project.org/bin/linux/ubuntu bionic-cran35/ InRelease [3,626 B]
Ign:2 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  InRelease
Get:3 http://security.ubuntu.com/ubuntu bionic-security InRelease [88.7 kB]
Ign:4 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  InRelease
Hit:5 https://developer.download.nvidia.com/compute/cuda/repos/ubuntu1804/x86_64  Release
Hit:6 https://developer.download.nvidia.com/compute/machine-learning/repos/ubuntu1804/x86_64  Release
Hit:7 http://ppa.launchpad.net/graphics-drivers/ppa/ubuntu bionic InRelease
Hit:9 http://archive.ubuntu.com/ubuntu bionic InRelease
Get:11 http://archive.ubuntu.com/ubuntu bionic-updates InRelease [88.7 kB]
Get:12 http://ppa.launchpad.net/marutter/c2d4u3.5/ubuntu bionic InRelease [15.4 kB]
Get:13 http://security.ubuntu.com/ubuntu bionic-security/main amd64 Packages [857 kB]
Get:14 http://archive.ubuntu.com/ubuntu bionic-backports InRelease [74.6 

In [0]:
from selenium import webdriver
options = webdriver.ChromeOptions()
options.add_argument('-headless')
options.add_argument('-no-sandbox')
options.add_argument('-disable-dev-shm-usage')

In [0]:
#2
driver = webdriver.Chrome('chromedriver',options=options)
import pandas as pd
import time
reviews=[]
username=[]
date=[]
driver.get('https://www.imdb.com/title/tt7286456/reviews')
for i in range(3):
  button=driver.find_element_by_xpath('/html[1]/body[1]/div[3]/div[1]/div[2]/div[3]/div[1]/section[1]/div[2]/div[4]/div[1]/button[1]').click()
  time.sleep(3)
items=driver.find_elements_by_class_name("content")
for item in items:
  reviews.append(item.find_element_by_css_selector('.text.show-more__control').text)
users=driver.find_elements_by_class_name("display-name-date")
for user in users:
  username.append(user.find_element_by_tag_name('a').text)
  date.append(user.find_element_by_class_name('review-date').text)
titles=driver.find_elements_by_class_name("lister-item-content")
reviews_df=pd.DataFrame(reviews, columns = ['Review'])
username_df=pd.DataFrame(username, columns = ['Username'])
date_df=pd.DataFrame(date, columns = ['Date'])
joker_data=pd.concat([date_df,username_df,reviews_df],axis=1)
joker_data.to_csv('output2.csv')
joker_data

Date  ...                                             Review
0   10 September 2019  ...  I was a person that saw all the hype and claim...
1      3 October 2019  ...  Every once in a while a movie comes, that trul...
2      7 October 2019  ...  This is a movie that only those who have felt ...
3    1 September 2019  ...  Truly a masterpiece, The Best Hollywood film o...
4      4 October 2019  ...  Most of the time movies are anticipated like t...
..                ...  ...                                                ...
95     4 October 2019  ...  Dark, depressing and unsettling film with a ha...
96     9 October 2019  ...  I just didn't get the hype about this movie. A...
97    19 October 2019  ...  Story was just really unconvincing. Nobody rea...
98     4 October 2019  ...  JOKER is a gift to the audiences. I felt as a ...
99   14 November 2019  ...  If you like movies with no story and 2 hours o...

[100 rows x 3 columns]

In [0]:
import nltk
nltk.download()

NLTK Downloader
---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> d

Download which package (l=list; x=cancel)?
  Identifier> all
       | 
       | Downloading package abc to /root/nltk_data...
       |   Unzipping corpora/abc.zip.
       | Downloading package alpino to /root/nltk_data...
       |   Unzipping corpora/alpino.zip.
       | Downloading package biocreative_ppi to /root/nltk_data...
       |   Unzipping corpora/biocreative_ppi.zip.
       | Downloading package brown to /root/nltk_data...
       |   Unzipping corpora/brown.zip.
       | Downloading package brown_tei to /root/nltk_data...
       |   Unzipping corpora/brown_tei.zip.
       | Downloading package cess_cat to /root/nltk_data...
       |   Unzipping corpora/cess_cat.zip.
       | Downloading package cess_esp to /root/nltk_data...
 

True

In [0]:
import regex as re
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.stem import PorterStemmer 
import pandas as pd
df = reviews_df['Review'].str.replace('[^\w\s#@/:%.,_-]', '', flags=re.UNICODE).to_frame()# 1.removed noise (special characters and punctuations)
df=df['Review'].str.replace('[^\w\s]','').replace('\n','', regex=True).to_frame()
no_nums=df['Review'].str.replace('\d+', '').to_frame()   # 2.Removed Numbers
lower = no_nums['Review'].str.lower().to_frame()  # 4.converted to lower case letters
stemmed=[]
lemmatized=[]
sentence=[]
stop_words = set(stopwords.words('english')) 
listed=lower['Review'].values.tolist()
for i in listed:
   word_tokens = word_tokenize(i) 
   filtered_sentence = [w for w in word_tokens if not w in stop_words] 
   filtered_sentence = []
   for w in word_tokens: 
     if w not in stop_words: 
         filtered_sentence.append(w)     # 3. Removed stop words
   sentence.append(' '.join(filtered_sentence))
cl_df=pd.DataFrame(sentence,columns=['Cleaned_data'])
cl_df.to_csv('output.csv')
ps = PorterStemmer() 
stemmed = []
for s in sentence:
    stemmed.append(" ".join([ps.stem(i) for i in s.split()]))       #5.Stemming
lemmatizer = WordNetLemmatizer() 
lemmatized=[]
for m in stemmed:
  lemmatized.append(" ".join([lemmatizer.lemmatize(i) for i in m.split()]))     #6.lemmatization
lemmatized_df=pd.DataFrame(lemmatized,columns=['Cleaned_data'])
data=lemmatized_df['Cleaned_data'].values.tolist()

In [0]:
#1.1
import itertools
from itertools import chain
from nltk import ngrams
from collections import Counter 
new=[]
data_string=''
for i in data:
  token_s = word_tokenize(i)
  new.append(token_s)
  data_string=data_string+' '+i
list2 = [x for x in new if x != []]
a=list(itertools.chain.from_iterable(list2))
one=ngrams(a,3)
Counter(one)

Counter({('person', 'saw', 'hype'): 1,
         ('saw', 'hype', 'claim'): 1,
         ('hype', 'claim', 'masterpiec'): 1,
         ('claim', 'masterpiec', 'overreact'): 1,
         ('masterpiec', 'overreact', 'overblown'): 1,
         ('overreact', 'overblown', 'excit'): 1,
         ('overblown', 'excit', 'anoth'): 1,
         ('excit', 'anoth', 'joker'): 1,
         ('anoth', 'joker', 'base'): 1,
         ('joker', 'base', 'film'): 1,
         ('base', 'film', 'thought'): 1,
         ('film', 'thought', 'look'): 1,
         ('thought', 'look', 'solid'): 1,
         ('look', 'solid', 'best'): 1,
         ('solid', 'best', 'even'): 1,
         ('best', 'even', 'bit'): 1,
         ('even', 'bit', 'pretenti'): 1,
         ('bit', 'pretenti', 'trailer'): 1,
         ('pretenti', 'trailer', 'say'): 1,
         ('trailer', 'say', 'incred'): 1,
         ('say', 'incred', 'wrong'): 1,
         ('incred', 'wrong', 'massiv'): 1,
         ('wrong', 'massiv', 'achiev'): 1,
         ('massiv', 'ach

In [0]:
pip install --upgrade nltk

     |████████████████████████████████| 1.5MB 2.7MB/s 
  Created wheel for nltk: filename=nltk-3.4.5-cp36-none-any.whl size=1449906 sha256=a79414d103cc6ec968704877a32de797fc47782fa41f5a5d272e4ffcf20c6286
  Stored in directory: /root/.cache/pip/wheels/96/86/f6/68ab24c23f207c0077381a5e3904b2815136b879538a24b483
Successfully built nltk
  Found existing installation: nltk 3.2.5
    Uninstalling nltk-3.2.5:
      Successfully uninstalled nltk-3.2.5


In [0]:
#1.2
from nltk import bigrams
from collections import Counter
gram_2=bigrams(a, pad_right=True, pad_left=True)
key_value=dict(Counter(gram_2))
m=0
for key in key_value:
  try:
    print(str(key)+'->',key_value.get(key)/a.count(key[1]))
  except:
    continue    #handled errors for none value

Streaming output truncated to the last 5000 lines.
('cinematographi', 'actor')-> 0.08333333333333333
('actor', 'score')-> 0.09090909090909091
('score', 'director')-> 0.16666666666666666
('director', 'get')-> 0.034482758620689655
('get', 'peopl')-> 0.022222222222222223
('peopl', 'hate')-> 0.2
('hate', 'polit')-> 1.0
('polit', 'messag')-> 0.16666666666666666
('messag', 'peopl')-> 0.022222222222222223
('peopl', 'think')-> 0.07692307692307693
('think', 'need')-> 0.10526315789473684
('need', 'get')-> 0.10344827586206896
('get', 'empathi')-> 1.0
('empathi', 'arthur')-> 0.0625
('arthur', 'mad')-> 0.5
('mad', 'come')-> 0.1
('come', 'point')-> 0.058823529411764705
('point', 'never')-> 0.125
('never', 'enjoy')-> 0.16666666666666666
('enjoy', 'masterpiec')-> 0.05
('masterpiec', 'joaquin')-> 0.021739130434782608
('phoenix', 'todd')-> 0.16666666666666666
('phillip', 'overdid')-> 1.0
('overdid', 'movi')-> 0.004149377593360996
('movi', 'actingmus')-> 1.0
('actingmus', 'cinematographi')-> 0.0588235294

In [0]:
pip install textacy

     |████████████████████████████████| 215kB 2.8MB/s 
     |████████████████████████████████| 3.0MB 8.7MB/s 
     |████████████████████████████████| 481kB 28.5MB/s 
     |████████████████████████████████| 143kB 25.0MB/s 
  Created wheel for cytoolz: filename=cytoolz-0.10.1-cp36-cp36m-linux_x86_64.whl size=1256643 sha256=16dc076fd0e23337c2a3265c80c17265fca7137262d5222a6c7a29ab6aa90393
  Stored in directory: /root/.cache/pip/wheels/64/2a/18/d962b614e055577e7d9a3e4813e0742f822ca9c8800cc3783a
  Created wheel for jellyfish: filename=jellyfish-0.7.2-cp36-cp36m-linux_x86_64.whl size=73004 sha256=1eb7d5efa52aeccbae43aedaee7d7a174344c40071a79e928286c99126d313aa
  Stored in directory: /root/.cache/pip/wheels/e8/fe/99/d8fa8f2ef7b82a625b0b77a84d319b0b50693659823c4effb4
Successfully built cytoolz jellyfish


In [0]:
s=''
for i in sentence:
  s=s+' '+i
doc_id=[]
for id in range(100):
  doc_id.append(str('Review_')+str(id))

In [0]:
import textacy
import pandas as pd
import itertools
phrases=[]
all_frequency=[]
noun_freq=[]
for i in sentence:
  noun_phrases=[]
  about_talk_doc = textacy.make_spacy_doc(i,lang='en_core_web_sm')
  for chunk in about_talk_doc.noun_chunks:
    noun_phrases.append(str(chunk))
  phrases.append(noun_phrases)
for i in phrases:
  for j in i:
    freq=[]
    for k in sentence:
      freq.append(k.count(j)/s.count(j))
    noun_freq.append(freq)
all_noun_phrase=list(itertools.chain.from_iterable(phrases))
df = pd.DataFrame(noun_freq).T
df.columns=all_noun_phrase
df.index=doc_id
df

person  hype  ...     joker    batman
Review_0   0.066667  0.10  ...  0.021898  0.000000
Review_1   0.000000  0.00  ...  0.000000  0.000000
Review_2   0.066667  0.00  ...  0.000000  0.000000
Review_3   0.000000  0.00  ...  0.007299  0.000000
Review_4   0.000000  0.05  ...  0.014599  0.000000
...             ...   ...  ...       ...       ...
Review_95  0.000000  0.00  ...  0.000000  0.000000
Review_96  0.000000  0.05  ...  0.000000  0.000000
Review_97  0.000000  0.05  ...  0.007299  0.000000
Review_98  0.066667  0.00  ...  0.007299  0.000000
Review_99  0.000000  0.00  ...  0.021898  0.058824

[100 rows x 1316 columns]

# **Question 2: Undersand TF-IDF and Document representation**

(40 points). Starting from the documents (all the reviews, or abstracts, or tweets) collected for assignment two, write a python program: 

(1) To build the **documents-terms weights (tf*idf) matrix bold text**.

(2) To rank the documents with respect to query (design a query by yourself, for example, "An Outstanding movie with a haunting performance and best character development") by using **cosine similarity**.

In [0]:
splits=[]
for i in sentence:          #splitted each sentence ->stored words in list -> converted to dictionary for updating the count
  splits.append(i.split(" "))
word_set=list(itertools.chain.from_iterable(splits))

In [0]:
a=[]
for split in splits:
  word_dict={}          
  word_dict=dict.fromkeys(word_set,0)
  for word in split:
    word_dict[word]+=1            #counted the frequency of word in each senetence and updated in different dictionary
  a.append(word_dict)

In [0]:
import pandas as pd
pd.DataFrame(a)

person  saw  hype  claims  ...  contain  cliffhangers  conclude  fighting
0        1    1     2       1  ...        0             0         0         0
1        0    0     0       0  ...        0             0         0         0
2        1    0     0       0  ...        0             0         0         0
3        0    0     0       0  ...        0             0         0         0
4        0    0     1       0  ...        0             0         0         0
..     ...  ...   ...     ...  ...      ...           ...       ...       ...
95       0    0     0       0  ...        0             0         0         0
96       0    0     1       0  ...        0             0         0         0
97       0    0     1       0  ...        0             0         0         0
98       1    0     0       0  ...        0             0         0         0
99       0    0     0       0  ...        1             1         1         1

[100 rows x 2164 columns]

In [0]:
def TF(w,list_sen):
  tfDict={}                     #calculated Term frequencies
  count_items=len(list_sen)
  for word,count in w.items():
    tfDict[word]=count/float(count_items)
  return tfDict

In [0]:
all_TF=[]                       #term frequencies for each document
for i in range(100):
  all_TF.append(TF(a[i],splits[i]))
all_TF

[{'person': 0.00980392156862745,
  'saw': 0.00980392156862745,
  'hype': 0.0196078431372549,
  'claims': 0.00980392156862745,
  'masterpiece': 0.0196078431372549,
  'overreacting': 0.00980392156862745,
  'overblown': 0.00980392156862745,
  'excitement': 0.00980392156862745,
  'another': 0.00980392156862745,
  'joker': 0.029411764705882353,
  'based': 0.00980392156862745,
  'film': 0.029411764705882353,
  'thought': 0.00980392156862745,
  'looked': 0.00980392156862745,
  'solid': 0.00980392156862745,
  'best': 0.0196078431372549,
  'even': 0.00980392156862745,
  'bit': 0.00980392156862745,
  'pretentious': 0.00980392156862745,
  'trailer': 0.00980392156862745,
  'say': 0.00980392156862745,
  'incredibly': 0.00980392156862745,
  'wrong': 0.00980392156862745,
  'massive': 0.00980392156862745,
  'achievement': 0.00980392156862745,
  'cinema': 0.0196078431372549,
  'thats': 0.00980392156862745,
  'extremely': 0.00980392156862745,
  'rare': 0.00980392156862745,
  'day': 0.00980392156862745,


In [0]:
import math                       # calculated IDF
def IDF(docList):
  idfDict={}
  n=len(docList)
  idfDict=dict.fromkeys(docList[0].keys(),0)
  for doc in docList:
    print(doc)
    for word,val in doc.items():
      if val>0:
        idfDict[word]+=1
  for word,val in idfDict.items():
    idfDict[word]=math.log(n/float(val))
  return idfDict

In [0]:
idfs=IDF(a)           
idfs

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{'person': 2.302585092994046,
 'saw': 2.995732273553991,
 'hype': 2.302585092994046,
 'claims': 3.912023005428146,
 'masterpiece': 1.9661128563728327,
 'overreacting': 4.605170185988092,
 'overblown': 4.605170185988092,
 'excitement': 3.912023005428146,
 'another': 2.8134107167600364,
 'joker': 0.7339691750802005,
 'based': 2.8134107167600364,
 'film': 1.3093333199837622,
 'thought': 2.407945608651872,
 'looked': 3.506557897319982,
 'solid': 3.912023005428146,
 'best': 1.4696759700589417,
 'even': 2.0402208285265546,
 'bit': 2.8134107167600364,
 'pretentious': 3.912023005428146,
 'trailer': 3.2188758248682006,
 'say': 1.6607312068216509,
 'incredibly': 3.506557897319982,
 'wrong': 2.8134107167600364,
 'massive': 3.912023005428146,
 'achievement': 3.506557897319982,
 'cinema': 2.302585092994046,
 'thats': 2.302585092994046,
 'extremely': 3.912023005428146,
 'rare': 4.605170185988092,
 'day': 3.506557897319982,
 'age': 4.605170185988092,
 'cgi': 3.506557897319982,
 'nonsense': 3.91202300

In [0]:
def TF_IDF(tf,idfs_data):         #calculated TF*IDF 
  tfidf={}
  for word,val in tf.items():
    tfidf[word]=val*idfs_data[word]
  return tfidf

In [0]:
all_tf_idf=[]                   #TF-IDF of all documents
for i in range(100):
  all_tf_idf.append(TF_IDF(all_TF[i],idfs))

In [0]:
pip install tabulate

In [0]:
from tabulate import tabulate
print(tabulate(pd.DataFrame(all_tf_idf), headers='keys', tablefmt='psql'))

+----+------------+------------+-----------+-----------+---------------+----------------+-------------+--------------+------------+------------+-----------+------------+-----------+-----------+-----------+------------+------------+------------+---------------+-----------+------------+--------------+------------+-----------+---------------+-----------+------------+-------------+-----------+-----------+-----------+------------+------------+-----------+------------+-----------+-----------+--------------+------------+-----------+--------------+-----------+-----------+-----------+---------------+-----------+------------+------------+-----------+-----------+-----------+------------+-----------+-----------------+-------------+---------------+-----------+-----------+------------+-----------+---------------+------------+------------+------------+-----------+-------------+-----------+-----------+-------------+-----------+------------+-----------+------------+--------------+-----------+----------

In [0]:
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize 
rank_set={}
count=0
for i in sentence:
  X =i
  Y='I am amazed I was shocked by how perfect Joaquins acting was I never imagined that I am going too see such a good interpretation of my favorite villain thank you for everything'
  X_list = word_tokenize(X) 
  Y_list = word_tokenize(Y) 
  sw = stopwords.words('english') 
  l1 =[];l2 =[] 
  X_set = {w for w in X_list if not w in sw} 
  Y_set = {w for w in Y_list if not w in sw} 
  rvector = X_set.union(Y_set) 
  for w in rvector:
    if w in X_set: l1.append(1) 
    else: l1.append(0) 
    if w in Y_set: l2.append(1) 
    else: l2.append(0) 
  c = 0
  for k in range(len(rvector)): 
    c+= l1[k]*l2[k] 
  try:
    cosine = c / float((sum(l1)*sum(l2))**0.5)
  except:
    cosine=0.0
  rank_set[count]=cosine
  count+=1 

In [0]:
import operator
import math
rank=[]
angles=[]
for i in range(100):
  max_value=max(rank_set.items(), key=operator.itemgetter(1))
  rank.append(max_value)
  del rank_set[max_value[0]]
for k in rank:
  angle_in_radians = math.acos(k[1])
  angles.append(math.degrees(angle_in_radians))
angles_docs=pd.DataFrame(angles,columns=['Angles'])
rem=pd.DataFrame(rank,columns=['Review_id','Similarity_using_cosine'])
ranks=pd.concat([rem,angles_docs],axis=1)
ranks.index.name='Ranks'
ranks

Review_id  Similarity_using_cosine     Angles
Ranks                                               
0             22                 0.129099  82.582444
1             40                 0.126773  82.716836
2             58                 0.121268  83.034723
3             89                 0.114708  83.413224
4             25                 0.111803  83.580716
...          ...                      ...        ...
95            86                 0.000000  90.000000
96            90                 0.000000  90.000000
97            91                 0.000000  90.000000
98            92                 0.000000  90.000000
99            98                 0.000000  90.000000

[100 rows x 3 columns]

# **Question 3: Create your own training and evaluation data for sentiment analysis**

(15 points). **You dodn't need to write program for this question!** Read each review (abstract or tweet) you collected in detail, and annotate each review with a sentiment (positive, negative, or neutral). Save the annotated dataset into a csv file with three columns (first column: document_id, clean_text, sentiment), upload the csv file to GitHub and submit the file link blew. This datset will be used for assignment four: sentiment analysis and text classification. 


In [0]:
# The GitHub link of your final csv file

 #Link: https://github.com/DeepakSaiPaty/Deepaksai_INFO5731_Spring2020/blob/master/Sentiment_analysis.csv